In [1]:
import numpy as np
import matplotlib.pyplot as plt
import torch
import torch.optim as optim

# x = torch.tensor(np.random.random([100]))
# x = np.random.random([100])
# plt.plot(x)
from tensorboardX import SummaryWriter
import torch.nn.functional as F

from tqdm import trange
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader
from kmeans_pytorch import kmeans
device = 'cuda:0'#'cpu'#

In [2]:
class MyDataset(Dataset):
    
    def __init__(self, x, y):
        self.x = x
        self.y = y
    
    def __len__(self):
        return self.x.size(0)
    
    def __getitem__(self, idx):
        x = self.x[idx]
        y = self.y[idx]
        return (x.to(torch.double).to(device), y.to(torch.double).to(device))
    

def error(a,b):
    return (0.5*torch.mean((a-b)**2))

In [3]:
# t = np.linspace(0,np.pi*2,1000)
# X_train = torch.tensor([np.sin(t),np.cos(t),np.sin(t)**2,np.sin(-t-np.pi/2)]).T.to(torch.double).to(device)
# Y_train = torch.tensor([np.sin(t)**3,np.cos(-t)**2]).T.to(torch.double).to(device)

# X_test = X_train
# Y_test = Y_train


# from sklearn.datasets import load_diabetes
# from sklearn.model_selection import train_test_split
# from sklearn import preprocessing
# import pandas as pd
# house_price = load_diabetes()
# df = pd.DataFrame(house_price.data, columns=house_price.feature_names)
# df['TEMP'] = house_price.target
# house_price.data = preprocessing.scale(house_price.data)
# X_train, X_test, Y_train, Y_test = train_test_split(
#     house_price.data, house_price.target, test_size=0.3, random_state=10)

# X_train = torch.tensor(X_train).to(device)
# X_test = torch.tensor(X_test).to(device)
# Y_train = torch.tensor(Y_train).unsqueeze(1).to(device)
# Y_test = torch.tensor(Y_test).unsqueeze(1).to(device)

# Y_train = torch.concat((Y_train,Y_train),1)
# Y_test = torch.concat((Y_test,Y_test),1)
# '''
import scipy.io as sc


temp1 = sc.loadmat('X.mat')
temp2 = sc.loadmat('Y.mat')
X_train = torch.tensor(temp1['X']['train'][0][0].T).to(torch.double).to(device)
Y_train = torch.tensor(temp2['Y']['train'][0][0].T).to(torch.double).to(device)
X_test = torch.tensor(temp1['X']['test'][0][0].T).to(torch.double).to(device)
Y_test = torch.tensor(temp2['Y']['test'][0][0].T).to(torch.double).to(device)
del temp1
del temp2
# '''
'''
Data=sc.loadmat('AkT.mat')
x=Data['Data']['X'][0][0]
y=Data['Data']['Y'][0][0]
ind=Data['Data']['ind'][0][0][:,0]
ind=np.concatenate((np.array([0]),ind))
X_train=torch.tensor(x[0:int(x.shape[0]*.8),:]).to(torch.double).to(device)#.T
X_test=torch.tensor(x[int(x.shape[0]*.8)::,:]).to(torch.double).to(device)#.T
Y_train=torch.tensor(y[0:int(x.shape[0]*.8),:]).to(torch.double).to(device)#.T
Y_test=torch.tensor(y[int(x.shape[0]*.8)::,:]).to(torch.double).to(device)#.T
del x
del y
'''

"\nData=sc.loadmat('AkT.mat')\nx=Data['Data']['X'][0][0]\ny=Data['Data']['Y'][0][0]\nind=Data['Data']['ind'][0][0][:,0]\nind=np.concatenate((np.array([0]),ind))\nX_train=torch.tensor(x[0:int(x.shape[0]*.8),:]).to(torch.double).to(device)#.T\nX_test=torch.tensor(x[int(x.shape[0]*.8)::,:]).to(torch.double).to(device)#.T\nY_train=torch.tensor(y[0:int(x.shape[0]*.8),:]).to(torch.double).to(device)#.T\nY_test=torch.tensor(y[int(x.shape[0]*.8)::,:]).to(torch.double).to(device)#.T\ndel x\ndel y\n"

In [4]:
# from FeatureExtraction import FeatureExtraction
import scipy.io as sc
import matplotlib.pyplot as plt
device = device
def error_rms(a,b):
    return 0.5*np.sqrt(np.sum((a-b)**2)/a.size)
def NRMSE(predicted_value,target_value):
	MSE=np.mean(np.power((predicted_value-target_value),2))
	RMSE=np.sqrt(MSE)
	P=target_value.shape[0]
	NRMSE=RMSE/np.sum((np.max(target_value,1)-np.min(target_value,1))/P)
	return NRMSE
# from M_RBFnn import *
# X = inputdata.T
# Y = targetdata.T




In [5]:
rem_ind = []
for i in range(X_train.shape[1]):
    if X_train[:,i].mean().cpu().numpy()==0:
        rem_ind.append(i)
k = 0
for i in rem_ind:
    X_train = torch.cat((X_train[:,:i-k],X_train[:,i+1-k:]),1)
    k+=1
rem_ind = []
for i in range(X_test.shape[1]):
    if X_test[:,i].mean().cpu().numpy()==0:
        rem_ind.append(i)
k = 0
for i in rem_ind:
    X_test = torch.cat((X_test[:,:i-k],X_test[:,i+1-k:]),1)
    k+=1

MEAN = torch.mean(X_train, dim = 0)
STD = torch.std(X_train, dim = 0)
X_train = (X_train-MEAN)/STD
X_test = (X_test-MEAN)/STD


In [6]:
# define pytorch device - useful for device-agnostic execution
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
import os
# define model parameters
NUM_EPOCHS = 90  # original paper
BATCH_SIZE = 128
MOMENTUM = 0.9
LR_DECAY = 0.0005
LR_INIT = 0.01
IMAGE_DIM = 227  # pixels
NUM_CLASSES = 1000  # 1000 classes for imagenet 2012 dataset
DEVICE_IDS = [0]#, 1, 2, 3]  # GPUs to use
# modify this to point to your data directory
# INPUT_ROOT_DIR = 'alexnet_data_in'
# TRAIN_IMG_DIR = 'alexnet_data_in/imagenet'
OUTPUT_DIR = 'log/Bi_LSTM'
LOG_DIR = OUTPUT_DIR + '/tblogs'  # tensorboard logs
CHECKPOINT_DIR = OUTPUT_DIR + '/models'  # model checkpoints

# make checkpoint path directory
os.makedirs(CHECKPOINT_DIR, exist_ok=True)
seed = torch.initial_seed()
print('Used seed : {}'.format(seed))

tbwriter = SummaryWriter(log_dir=LOG_DIR)
print('TensorboardX summary writer created')

Used seed : 253479533031400
TensorboardX summary writer created


In [7]:
# X_train = X_train[0:24000]
# Y_train = Y_train[0:24000]

In [7]:
class BiLSTMModel(nn.Module):
    def __init__(self, input_size, hidden_size=250, num_layers=1, num_classes=2):
        super(BiLSTMModel, self).__init__()
        
        # Define the Bidirectional LSTM layers
        self.lstm1 = nn.LSTM(input_size, hidden_size, num_layers, batch_first=True, bidirectional=True)
        self.lstm2 = nn.LSTM(2 * hidden_size, hidden_size, num_layers, batch_first=True, bidirectional=True)

        # Define the fully connected layer
        self.fc = nn.Linear(2 * hidden_size, num_classes)

    def forward(self, x):
        # Forward pass through the first LSTM layer
        out, _ = self.lstm1(x)
        
        # Forward pass through the second LSTM layer
        out, _ = self.lstm2(out)
        
        # print(out.shape)
        # Get the output from the last time step
        # out = out[:, -1, :]

        # Apply the fully connected layer
        out = self.fc(out)

        return out

# Define the input size, hidden size, number of layers, and number of classes
input_size = X_train.shape[1]  # Adjust based on your input data size
hidden_size = 250#128
num_layers = 1  # You can increase the number of layers if needed
num_classes = Y_train.shape[1]  # Adjust based on your problem

# Create the model
model = BiLSTMModel(input_size, hidden_size, num_layers, num_classes).to(torch.double).to(device)

# Print the model architecture
print(model)

# model = BiLSTMModel(X_train.shape[1], 20, 250 , Y_train.shape[1]).to(torch.double).to(device)


BiLSTMModel(
  (lstm1): LSTM(104, 250, batch_first=True, bidirectional=True)
  (lstm2): LSTM(500, 250, batch_first=True, bidirectional=True)
  (fc): Linear(in_features=500, out_features=6, bias=True)
)


In [9]:
trainset = MyDataset(X_train, Y_train)
batch_size = 128#*64
dataloader = DataLoader(trainset, batch_size=batch_size, shuffle=True)
print('Dataloader created')

optimizer = optim.Adam(params=model.parameters(), lr=0.0001)
### BELOW is the setting proposed by the original paper - which doesn't train....
# optimizer = optim.SGD(
#     params=alexnet.parameters(),
#     lr=LR_INIT,
#     momentum=MOMENTUM,
#     weight_decay=LR_DECAY)
print('Optimizer created')

# multiply LR by 1 / 10 after every 30 epochs
lr_scheduler = optim.lr_scheduler.StepLR(optimizer, step_size=30, gamma=0.1)
print('LR Scheduler created')

# start training!!
print('Starting training...')
total_steps = 1
for epoch in range(NUM_EPOCHS):
    lr_scheduler.step()
    for imgs, classes in dataloader:
        imgs, classes = imgs, classes

        # calculate the loss
        output = model(imgs)
        loss = F.mse_loss(output, classes)#cross_entropy

        # update the parameters
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        # log the information and add to tensorboard
        # if total_steps % 10 == 0:
        with torch.no_grad():
            _, preds = torch.max(output, 1)
            # accuracy = torch.sum(preds == classes)

            print('Epoch: {} \tStep: {} \tLoss: {:.4f} '#\tAcc: {}
                .format(epoch + 1, total_steps, loss.item()))#, accuracy.item()
            tbwriter.add_scalar('loss', loss.item(), total_steps)
            # tbwriter.add_scalar('accuracy', accuracy.item(), total_steps)

        total_steps += 1

    # save checkpoints
    # checkpoint_path = os.path.join(CHECKPOINT_DIR, 'alexnet_states_e{}.pkl'.format(epoch + 1))
    checkpoint_path = os.path.join(CHECKPOINT_DIR, 'Bi_LSTM{}.pt'.format(epoch + 1))
    # state = {
    #     'epoch': epoch,
    #     'total_steps': total_steps,
    #     'optimizer': optimizer.state_dict(),
    #     'model': model.state_dict(),
    #     'seed': seed,
    # }
    torch.save(model, checkpoint_path)

Dataloader created
Optimizer created
LR Scheduler created
Starting training...
Epoch: 1 	Step: 1 	Loss: 0.0510 


c:\Users\kiano\.conda\envs\py38\lib\site-packages\torch\optim\lr_scheduler.py:139: UserWarning: Detected call of `lr_scheduler.step()` before `optimizer.step()`. In PyTorch 1.1.0 and later, you should call them in the opposite order: `optimizer.step()` before `lr_scheduler.step()`.  Failure to do this will result in PyTorch skipping the first value of the learning rate schedule. See more details at https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate
  warnings.warn("Detected call of `lr_scheduler.step()` before `optimizer.step()`. "


Epoch: 1 	Step: 2 	Loss: 0.0483 
Epoch: 1 	Step: 3 	Loss: 0.0459 
Epoch: 1 	Step: 4 	Loss: 0.0426 
Epoch: 1 	Step: 5 	Loss: 0.0391 
Epoch: 1 	Step: 6 	Loss: 0.0400 
Epoch: 1 	Step: 7 	Loss: 0.0381 
Epoch: 1 	Step: 8 	Loss: 0.0348 
Epoch: 1 	Step: 9 	Loss: 0.0325 
Epoch: 1 	Step: 10 	Loss: 0.0316 
Epoch: 1 	Step: 11 	Loss: 0.0327 
Epoch: 1 	Step: 12 	Loss: 0.0288 
Epoch: 1 	Step: 13 	Loss: 0.0264 
Epoch: 1 	Step: 14 	Loss: 0.0281 
Epoch: 1 	Step: 15 	Loss: 0.0247 
Epoch: 1 	Step: 16 	Loss: 0.0253 
Epoch: 1 	Step: 17 	Loss: 0.0259 
Epoch: 1 	Step: 18 	Loss: 0.0252 
Epoch: 1 	Step: 19 	Loss: 0.0241 
Epoch: 1 	Step: 20 	Loss: 0.0243 
Epoch: 1 	Step: 21 	Loss: 0.0203 
Epoch: 1 	Step: 22 	Loss: 0.0207 
Epoch: 1 	Step: 23 	Loss: 0.0221 
Epoch: 1 	Step: 24 	Loss: 0.0234 
Epoch: 1 	Step: 25 	Loss: 0.0229 
Epoch: 1 	Step: 26 	Loss: 0.0225 
Epoch: 1 	Step: 27 	Loss: 0.0217 
Epoch: 1 	Step: 28 	Loss: 0.0208 
Epoch: 1 	Step: 29 	Loss: 0.0206 
Epoch: 1 	Step: 30 	Loss: 0.0207 
Epoch: 1 	Step: 31 	Lo

In [10]:
Y_hat = model.forward(X_train[0:6000])
plt.plot(Y_train[0:6000,0].cpu().numpy())
plt.plot(Y_hat[0:6000,0].cpu().detach().numpy())


: 

In [8]:
model = torch.load('./log/Bi_LSTM/models/Bi_LSTM90.pt')

In [9]:
# torch.save(model,'./log/Bi_LSTM/models/Bi_LSTM90.pth')

In [21]:
y_hat = model.forward(X_test)

In [18]:
NRMSE(Y_train.detach().cpu().numpy(), y_hat.detach().cpu().numpy())

0.07510860157026093

In [22]:
def PCC(predicted_output, desired_output):
    # Calculate the mean of predicted and desired outputs
    mean_predicted = torch.mean(predicted_output)
    mean_desired = torch.mean(desired_output)

    # Calculate the Pearson correlation coefficient
    numerator = torch.sum((predicted_output - mean_predicted) * (desired_output - mean_desired))
    denominator_predicted = torch.sqrt(torch.sum((predicted_output - mean_predicted)**2))
    denominator_desired = torch.sqrt(torch.sum((desired_output - mean_desired)**2))
    pcc = numerator / (denominator_predicted * denominator_desired)

    # Print the result
    print("Pearson Correlation Coefficient:", pcc.item())
PCC(Y_test.detach().cpu(), y_hat.detach().cpu())

Pearson Correlation Coefficient: 0.9034988184671633


In [23]:
Y_hat = model.forward(X_test[10000:16000]).cpu().detach().numpy()
yy = Y_test[10000:16000,0].cpu().numpy()

